# Automatic calibration of SWMM project 
#### Written by: Abullqasim Shakeri



## Import necessary packages and libraries




In [1]:
import pandas as pd

from datetime import datetime
from datetime import timedelta

from swmm_api import read_out_file
from swmm_api.output_file.out import VARIABLES, OBJECTS

from pyswmm import Simulation, Links, Subcatchments




## Read and write some necessary files from the project folder

In [2]:
# Parameters and there ranges
ranges = pd.read_excel(r'Ranges.xlsx')


# Reading Observed Data
observed = pd.read_csv(r'Observed_flows.csv')
observed['date and time'] = pd.to_datetime(observed['Date'] + " " + observed['Time'], format='%m/%d/%Y %H:%M:%S')
observed['date and time2'] = pd.to_datetime(observed['Date'] + " " + observed['Time'], format='%m/%d/%Y %H:%M:%S')
observed.set_index("date and time2", inplace=True)


# Create a new data frame files in order to store new calibrated values
Calibration = pd.DataFrame(
    columns=["Rain_Events", "Subcatchment", "Imperviousness", "width", "Slope", "NSE_L1", "NSE_L2", "PFE_L1", "PFE_L2"])
Calibrated_sub = pd.DataFrame(
    columns=["Rain_Events", "Subcatchment", "Imperviousness", "width", "Slope", "NSE_L1", "NSE_L2", "PFE_L1", "PFE_L2"])
Calibrated_rain_event = pd.DataFrame(
    columns=["Rain_Events", "Subcatchment", "Imperviousness", "width", "Slope", "NSE_L1", "NSE_L2", "PFE_L1", "PFE_L2"])
Line = 55
Sub_N = 0
inde = 0

## Some new written functions

In [8]:
# To calculate NSE
def nse_f(calculated, observed_flow):
    numerator = (calculated - observed_flow) ** 2
    denominator = (observed_flow - observed_flow.mean()) ** 2
    nse = 1 - (numerator.sum() / denominator.sum())
    return nse



 # To calculate PFE
def pfe_f(calculated, observed_flow):
    pfe = abs((observed_flow.max() - calculated.max()) / observed_flow.max())
    return pfe




# To read out file and return value of link flow for the given out file. 
def read_out(name):
    out = read_out_file(name)
    outputfile = out.to_frame()
    pd.set_option("display.max_columns", None)

    link_1 = out.get_part(OBJECTS.LINK, '06L95-06L98', VARIABLES.LINK.FLOW_RATE).to_frame()
    link_2 = out.get_part(OBJECTS.LINK, '06M5-06M4', VARIABLES.LINK.FLOW_RATE).to_frame()
    link_1_2 = pd.concat([link_1, link_2], axis=1)
    link_flow = link_1_2[:End_date]
    return link_flow




# To assign new date for rain event
def time_assign(year, month, day):
    sim.step_advance(300)
    sim.start_time = datetime(year, month, day - 1, 0, 0, 0)
    sim.report_start = datetime(year, month, day, 0, 0, 0)
    sim.end_time = datetime(year, month, day + 1, 23, 55, 0)

    
    
    
# To run the model
def model_run():
    l1 = Links(sim)["06L95-06L98"]
    l2 = Links(sim)["06M5-06M4"]
    link_flow_df = pd.DataFrame(columns=["Date and time", "flow_L1", "flow_L2"])

    for step in sim:
        link_flow = sim.current_time, l1.flow
        link_flow = sim.current_time, l2.flow
        link_flow_df = link_flow_df.append({"Date and time": sim.current_time, "flow_L1": l1.flow, "flow_L2": l2.flow},
                                           ignore_index=True)

        
        
        
# To replace imperviousness value in the source .inp file
def imper_replace(perc_imper, ):
    imper_n = pd.read_csv('imper.csv')
    Name_imper = imper_n["Name"][Sub_N]
    Rain_gage_imper = "RG"
    outlet_imper = imper_n["Outlet"][Sub_N]
    Area_imper = imper_n["Area"][Sub_N]
    Perc_imper = perc_imper
    Width_imper = Width_Orig
    Perc_slope_imper = Slope_orig
    Curblen_imper = "0"
    New_line = f"{Name_imper}             {Rain_gage_imper}               {outlet_imper}             {Area_imper}     {Perc_imper}          {Width_imper}      {Perc_slope_imper}     {Curblen_imper}\n"
    my_file = open("TUD_sewer_v9.inp")
    string_list = my_file.readlines()
    my_file.close()
    string_list[Line] = str(New_line)
    my_file = open("TUD_sewer_v9.inp", "w")
    new_file_contents = "".join(string_list)
    my_file.write(new_file_contents)
    my_file.close()
    readable_file = open("TUD_sewer_v9.inp")
    read_file = readable_file.read()


# Calibration process for all given rain event and catchments

In [4]:
Rain_N = 0
while Rain_N <= 42:

    Line = 55

    Sub_N = 0  # catchment

    wb = pd.read_excel(r'Dates_events.xlsx')
    year = wb.at[Rain_N, "year"]
    month = wb.at[Rain_N, "month"]
    day = wb.at[Rain_N, "Day"]

    print(year, month, day, 0, 0, 0)

    # Rain event from CSV
    rain_event = pd.read_csv(r'Dates_events_calibration.csv')
    rain_event["D and T"] = pd.to_datetime(rain_event["D and T"])

    # Select the observed data
    Start_date = rain_event.loc[Rain_N]["D and T"]
    End_date = Start_date + timedelta(days=1)
    after_start_date = observed["date and time"] >= Start_date
    before_end_date = observed["date and time"] <= End_date
    between_two_dates = after_start_date & before_end_date
    filtered_dates = observed.loc[between_two_dates]

    while Sub_N <= 18:
        with Simulation('TUD_sewer_v9.inp') as sim:
            # Setting start time and time step for simulation of the selected Subcatchment
            time_assign(year, month, day)
            
            SubID = ranges.at[Sub_N, "Subcatchment"]
            Subca = Subcatchments(sim)[str(SubID)]

            model_run()

            Link_flow = read_out('TUD_sewer_v9.out')
            NSE_L1 = nse_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
            PFE_L1 = pfe_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
            NSE_L2 = nse_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])
            PFE_L2 = pfe_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])
            New_data = {"Rain_Events": Start_date, "Subcatchment": Subca.subcatchmentid,
                        "Imperviousness": Subca.percent_impervious,
                        "width": Subca.width, "Slope": Subca.slope, "NSE_L1": NSE_L1, "NSE_L2": NSE_L2,
                        "PFE_L1": PFE_L1,
                        "PFE_L2": PFE_L2}

            # Storing NSE and PFE values for the selected parameters into a new dataframe file
            Calibration = Calibration.append(New_data, ignore_index=True)

            # value selection for each parameter from ranges excel file
            Slope_orig = Subca.slope * 100
            Imper_Orig = Subca.percent_impervious * 100
            Width_Orig = Subca.width

            NSE_L1_Orig = NSE_L1
            NSE_L2_Orig = NSE_L2
            PFE_L1_Orig = PFE_L1
            PFE_L2_Orig = PFE_L2

        col_1 = 1
        while col_1 <= 5:  # loop for Imperviousness value selection for the selected subcatchment
            # Replacing new value for the Impervouseness in the source SWMM.INP file of the model
            imper_replace(ranges.at[Sub_N, "Imperviousness_" + str(col_1)])

            # Runing model for the new replaced value
            from pyswmm import Simulation, Subcatchments

            with Simulation('TUD_sewer_v9.inp') as sim:
                # Setting start time and time step for simulation of the selected Subcathcment
                time_assign(year, month, day)

                SubID = ranges.at[Sub_N, "Subcatchment"]
                Subca = Subcatchments(sim)[str(SubID)]
                Subca.percent_impervious = ranges.at[Sub_N, "Imperviousness_" + str(col_1)]

                model_run()

                Link_flow = read_out('TUD_sewer_v9.out')
                NSE_L1 = nse_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
                PFE_L1 = pfe_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
                NSE_L2 = nse_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])
                PFE_L2 = pfe_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])

                New_data = {"Rain_Events": Start_date, "Subcatchment": Subca.subcatchmentid,
                            "Imperviousness": Subca.percent_impervious,
                            "width": Subca.width, "Slope": Subca.slope, "NSE_L1": NSE_L1, "NSE_L2": NSE_L2,
                            "PFE_L1": PFE_L1,
                            "PFE_L2": PFE_L2}
                # Storing NSE and PFE values for the selected subcatchment and parameters into a new dataframe file
                Calibration = Calibration.append(New_data, ignore_index=True)

                # condition in order to keep the new values added to the parameters or not, according to the achieved NSE and PFE value
                if NSE_L2 >= NSE_L2_Orig and PFE_L2 <= PFE_L2_Orig and NSE_L1 >= NSE_L1_Orig and PFE_L1 <= PFE_L1_Orig:
                    Imper_Orig = Subca.percent_impervious * 100

                col_1 = col_1 + 1

        col_1 = 1
        while col_1 <= 5:  # loop for width value selection for the selected Subcatchment
            # Replacing new value for the width in the source SWMM.INP file of the model
            with Simulation('TUD_sewer_v9.inp') as sim:
                # Setting start time and time step for simulation
                time_assign(year, month, day)

                SubID = ranges.at[Sub_N, "Subcatchment"]
                Subca = Subcatchments(sim)[str(SubID)]
                Subca.percent_impervious = Imper_Orig
                Subca.width = ranges.at[Sub_N, "Width_" + str(col_1)]

                model_run()

                Link_flow = read_out('TUD_sewer_v9.out')
                NSE_L1 = nse_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
                PFE_L1 = pfe_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
                NSE_L2 = nse_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])
                PFE_L2 = pfe_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])

                New_data = {"Rain_Events": Start_date, "Subcatchment": Subca.subcatchmentid,
                            "Imperviousness": Subca.percent_impervious,
                            "width": Subca.width, "Slope": Subca.slope, "NSE_L1": NSE_L1, "NSE_L2": NSE_L2,
                            "PFE_L1": PFE_L1,
                            "PFE_L2": PFE_L2}

                # Storing NSE and PFE values for the selected subcatchment and parameters into a new dataframe file
                Calibration = Calibration.append(New_data, ignore_index=True)

                # condition in order to keep the new values added to the parameters or not, according to the achieved NSE and PFE value
                if NSE_L2 >= NSE_L2_Orig and PFE_L2 <= PFE_L2_Orig and NSE_L1 >= NSE_L1_Orig and PFE_L1 <= PFE_L1_Orig:
                    Width_Orig = Subca.width

                col_1 = col_1 + 1
                
        col_1 = 1
        while col_1 <= 5:  # loop for slope value selection for the selected Subcatchment
            # Replacing new value for the slope in the source SWMM.INP file of the model
            with Simulation('TUD_sewer_v9.inp') as sim:
                # Setting start time and time step for simulation of the selected Subcathcment
                time_assign(year, month, day)

                SubID = ranges.at[Sub_N, "Subcatchment"]
                Subca = Subcatchments(sim)[str(SubID)]
                Subca.width = Width_Orig
                Subca.percent_impervious = Imper_Orig
                Subca.slope = ranges.at[Sub_N, "Slope_" + str(col_1)] / 100

                model_run()

                # Reading output file for Link flow results
                Link_flow = read_out('TUD_sewer_v9.out')
                NSE_L1 = nse_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
                PFE_L1 = pfe_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
                NSE_L2 = nse_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])
                PFE_L2 = pfe_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])

                New_data = {"Rain_Events": Start_date, "Subcatchment": Subca.subcatchmentid,
                            "Imperviousness": Subca.percent_impervious,
                            "width": Subca.width, "Slope": Subca.slope, "NSE_L1": NSE_L1, "NSE_L2": NSE_L2,
                            "PFE_L1": PFE_L1,
                            "PFE_L2": PFE_L2}

                # Storing NSE and PFE values for the selected parameters into a new dataframe file
                Calibration = Calibration.append(New_data, ignore_index=True)

                # condition in order to keep the new values added to the parameters or not, according to the achieved NSE and PFE value
                if NSE_L2 >= NSE_L2_Orig and PFE_L2 <= PFE_L2_Orig and NSE_L1 >= NSE_L1_Orig and PFE_L1 <= PFE_L1_Orig:
                    Slope_orig = Subca.slope * 100

                col_1 = col_1 + 1
                                

        imper_replace(Imper_Orig)
        with Simulation('TUD_sewer_v9.inp') as sim:

            time_assign(year, month, day)

            SubID = ranges.at[Sub_N, "Subcatchment"]
            Subca = Subcatchments(sim)[str(SubID)]

            model_run()

            Link_flow = read_out('TUD_sewer_v9.out')
            NSE_L1 = nse_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
            PFE_L1 = pfe_f(Link_flow["link/06L95-06L98/Flow_rate"], filtered_dates["06L95-06L98"])
            NSE_L2 = nse_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])
            PFE_L2 = pfe_f(Link_flow["link/06M5-06M4/Flow_rate"], filtered_dates["06M5-06M4 "])
            New_data = {"Rain_Events": Start_date, "Subcatchment": Subca.subcatchmentid,
                        "Imperviousness": Subca.percent_impervious,
                        "width": Subca.width, "Slope": Subca.slope, "NSE_L1": NSE_L1, "NSE_L2": NSE_L2,
                        "PFE_L1": PFE_L1,
                        "PFE_L2": PFE_L2}
            Calibrated_sub = Calibrated_sub.append(New_data, ignore_index=True)
            print(Subca.subcatchmentid)

        Sub_N = Sub_N + 1
        Line = Line + 1
        
    Rain_N = Rain_N + 1
# Creating a new CSV file for the stored Calibrated data
# Creating a new CSV file for the stored Calibrated data
Calibration.to_csv('Calibration.csv')
Calibrated_sub.to_csv("Calibrated_sub.csv")


1996 5 4 0 0 0


C:\Users\Abullqasim\anaconda3\lib\site-packages\swmm_api\output_file\extract.py:142: SwmmOutExtractWarning: Ending magic number incorrect.
  warn('Ending magic number incorrect.', SwmmOutExtractWarning)
C:\Users\Abullqasim\anaconda3\lib\site-packages\swmm_api\output_file\extract.py:239: SwmmOutExtractWarning: Infer time periods of the output file due to an corrupt SWMM .out-file.
  warn('Infer time periods of the output file due to an corrupt SWMM .out-file.', SwmmOutExtractWarning)


101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1996 6 3 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1996 7 8 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1996 8 11 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1996 8 11 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1996 8 22 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1997 7 18 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1997 7 25 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1998 6 3 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1998 7 21 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1998 9 12 0 0 0
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
1999 7 

# Result for each time iteration 

#### a .csv file of this result is created at project folder with the file name (Calibration.csv)


In [13]:
pd.set_option("display.max_rows", None, "display.max_columns", None)
Calibration

Rain_Events Subcatchment  Imperviousness       width   Slope    NSE_L1  \
0      1996-05-04          101        0.582354   80.689336  0.0050  0.842187   
1      1996-05-04          101        0.330000   80.689336  0.0050  0.842187   
2      1996-05-04          101        0.497500   80.689336  0.0050  0.842187   
3      1996-05-04          101        0.665000   80.689336  0.0050  0.842187   
4      1996-05-04          101        0.832500   80.689336  0.0050  0.842187   
5      1996-05-04          101        1.000000   80.689336  0.0050  0.842187   
6      1996-05-04          101        1.000000  190.000000  0.0050  0.842187   
7      1996-05-04          101        1.000000  285.000000  0.0050  0.842187   
8      1996-05-04          101        1.000000  380.000000  0.0050  0.842187   
9      1996-05-04          101        1.000000  475.000000  0.0050  0.842187   
10     1996-05-04          101        1.000000  570.000000  0.0050  0.842187   
11     1996-05-04          101        1.000000  570.000000  0.0100  0.842188   
12     1996-05-04          101        1.000000  570.000000  0.0175  0.842182   
13     1996-05-04          101        1.000000  570.000000  0.0250  0.842187   
14     1996-05-04          101        1.000000  570.000000  0.0325  0.842168   
15     1996-05-04          101        1.000000  570.000000  0.0400  0.842177   
16     1996-05-04          102        0.099636  197.603228  0.0050  0.842188   
17     1996-05-04          102        0.200000  197.603228  0.0050  0.842189   
18     1996-05-04          102        0.312500  197.603228  0.0050  0.842189   
19     1996-05-04          102        0.425000  197.603228  0.0050  0.842189   
20     1996-05-04          102        0.537500  197.603228  0.0050  0.842190   
21     1996-05-04          102        0.650000  197.603228  0.0050  0.842190   
22     1996-05-04          102        0.650000   56.000000  0.0050  0.842190   
23     1996-05-04          102        0.650000   83.750000  0.0050  0.842191   
24     1996-05-04          102        0.650000  111.500000  0.0050  0.842190   
25     1996-05-04          102        0.650000  139.250000  0.0050  0.842190   
26     1996-05-04          102        0.650000  167.000000  0.0050  0.842190   
27     1996-05-04          102        0.650000  167.000000  0.0100  0.842190   
28     1996-05-04          102        0.650000  167.000000  0.0125  0.842190   
29     1996-05-04          102        0.650000  167.000000  0.0150  0.842190   
30     1996-05-04          102        0.650000  167.000000  0.0175  0.842190   
31     1996-05-04          102        0.650000  167.000000  0.0200  0.842191   
32     1996-05-04          103        0.194177  296.495361  0.0050  0.842191   
33     1996-05-04          103        0.180000  296.495361  0.0050  0.842190   
34     1996-05-04          103        0.277500  296.495361  0.0050  0.842191   
35     1996-05-04          103        0.375000  296.495361  0.0050  0.842189   
36     1996-05-04          103        0.472500  296.495361  0.0050  0.842185   
37     1996-05-04          103        0.570000  296.495361  0.0050  0.842185   
38     1996-05-04          103        0.570000   70.000000  0.0050  0.842189   
39     1996-05-04          103        0.570000  104.750000  0.0050  0.842188   
40     1996-05-04          103        0.570000  139.500000  0.0050  0.842189   
41     1996-05-04          103        0.570000  174.250000  0.0050  0.842190   
42     1996-05-04          103        0.570000  209.000000  0.0050  0.842190   
43     1996-05-04          103        0.570000  296.495361  0.0300  0.842190   
44     1996-05-04          103        0.570000  296.495361  0.0425  0.842181   
45     1996-05-04          103        0.570000  296.495361  0.0550  0.842194   
46     1996-05-04          103        0.570000  296.495361  0.0675  0.842182   
47     1996-05-04          103        0.570000  296.495361  0.0800  0.842171   
48     1996-05-04          104        0.091350  139.419916  0.0050  0.842168   
49    

## Final calibrated values for each subcatchments and their respective rain events
#### a .csv file of this result is created at project folder with the file name (Calibrated_sub.csv)

In [15]:
Calibrated_sub

Rain_Events Subcatchment  Imperviousness       width  Slope    NSE_L1  \
0    1996-05-04          101        1.000000  570.000000  0.010  0.842188   
1    1996-05-04          102        0.650000  167.000000  0.020  0.842191   
2    1996-05-04          103        0.277500  296.495361  0.055  0.842168   
3    1996-05-04          104        0.091350  139.419916  0.005  0.842168   
4    1996-05-04          105        0.198253   78.683089  0.005  0.842168   
5    1996-05-04          106        0.179188  306.000000  0.070  0.842180   
6    1996-05-04          107        0.460000  116.000000  0.050  0.842190   
7    1996-05-04          108        0.105867   72.000000  0.010  0.842190   
8    1996-05-04          109        0.223563   85.689641  0.005  0.842190   
9    1996-05-04          110        0.137500  183.292937  0.005  0.879875   
10   1996-05-04          111        0.150000  148.553152  0.005  0.880787   
11   1996-05-04          112        0.162270  128.255000  0.005  0.880787   
12   1996-05-04          113        0.411348   99.859140  0.005  0.880787   
13   1996-05-04          114        0.272394  101.592500  0.005  0.880787   
14   1996-05-04          115        1.000000  313.500000  0.005  0.880787   
15   1996-05-04          116        1.000000   20.297931  0.005  0.880787   
16   1996-05-04          117        1.000000  316.516505  0.005  0.880787   
17   1996-05-04          118        1.000000  336.940385  0.005  0.880787   
18   1996-05-04          119        0.460000  414.879231  0.020  0.891980   
19   1996-06-03          101        1.000000  570.000000  0.010  0.905248   
20   1996-06-03          102        0.650000  167.000000  0.020  0.905248   
21   1996-06-03          103        0.277500  296.495361  0.055  0.905248   
22   1996-06-03          104        0.091350  139.419916  0.005  0.905248   
23   1996-06-03          105        0.182500   78.683089  0.005  0.905248   
24   1996-06-03          106        0.179188  306.000000  0.070  0.905248   
25   1996-06-03          107        0.460000  116.000000  0.050  0.905248   
26   1996-06-03          108        0.100000   72.000000  0.010  0.905248   
27   1996-06-03          109        0.223563   85.689641  0.005  0.905248   
28   1996-06-03          110        0.137500  183.292937  0.005  0.905248   
29   1996-06-03          111        0.150000  148.553152  0.005  0.905248   
30   1996-06-03          112        0.142500  128.255000  0.005  0.905821   
31   1996-06-03          113        0.320000   99.859140  0.005  0.906317   
32   1996-06-03          114        0.272394   74.250000  0.005  0.906501   
33   1996-06-03          115        1.000000  313.500000  0.005  0.906501   
34   1996-06-03          116        1.000000   20.297931  0.005  0.906501   
35   1996-06-03          117        1.000000   18.000000  0.045  0.906581   
36   1996-06-03          118        1.000000  336.940385  0.005  0.906581   
37   1996-06-03          119        0.460000  414.879231  0.020  0.906581   
38   1996-07-08          101        1.000000  570.000000  0.040  0.969433   
39   1996-07-08          102        0.650000  167.000000  0.020  0.969433   
40   1996-07-08          103        0.277500  296.495361  0.055  0.969433   
41   1996-07-08          104        0.091350  139.419916  0.005  0.969433   
42   1996-07-08          105        0.220000  212.000000  0.100  0.969433   
43   1996-07-08          106        0.179188  306.000000  0.070  0.969433   
44   1996-07-08          107        0.460000  116.000000  0.050  0.969433   
45   1996-07-08          108        0.120000  216.000000  0.040  0.969434   
46   1996-07-08          109        0.223563   85.689641  0.005  0.969434   
47   1996-07-08          110        0.137500  183.292937  0.005  0.969434   
48   1996-07-08          111        0.150000  148.553152  0.005  0.969434   
49   1996-07-08          112        0.142500  128.255000  0.005  0.969434   
50   1996-07-08          113        0.320000   99.859140  0.005  0.969434   
